In [3]:
import numpy as np
import sys
#give first vocabulary it will give following stances

In [ ]:
# small data check
# grad check
def grad_check():
    

In [211]:
# define loss func
def lossFunc(inputs, targets, hprev):
    # forward
    h_train[-1] = np.zeros(hidden_size)
    loss = 0
    for t in range(len(inputs)):
        x_train[t] = np.zeros([1, len(voc_sets)]) # 1, C
        x_train[t][0, inputs[t]] = 1 # OneHot
        # linear layer (hs = Whh*h0 + Whx*x + bx)
        h_lin[t] = x_train[t].dot(Whx) + h_train[t-1].dot(Whh) + bx
        # nonlinear tanh layer
        h_train[t] = np.tanh(h_lin[t])
        # linear layer for scores
        y_train[t] = h_train[t].dot(Why) + by # 1, C
        # softmax layer (1, C)
        prob_train[t] = np.exp(y_train[t])/np.sum(np.exp(y_train[t]))
        #print(prob_train[t])
        loss += -np.log(prob_train[t][0, targets[t]])

    # backward
    #dh_train[len(inputs)]=np.zeros_like(h_train[0])
    dh_next = np.zeros_like(h_train[0])
    dWhx, dWhh, dWhy = np.zeros_like(Whx), np.zeros_like(Whh), np.zeros_like(Why)
    dbx, dby = np.zeros_like(bx), np.zeros_like(by)
    for t in range(len(inputs)-1, 0, -1):
        # softmax grad
        # dh, dy don't need to store so not use dict
        dy = prob_train[t] # N(1), C
        #print(dy,dy.shape, targets[t])
        dy[0, targets[t]] -= 1
        # score linear grad. dW, db not depend on t
        dWhy += h_train[t].T.dot(dy) # (N, H)^T * (N, C)= (H, C)
        dby += dy # (1, C)
        #dh_train[t] = dh_train[t+1].dot(Whh) + dy[t].dot(Why.T) #(N, H)*(H, H) * (N,C) * (H,C)^T = (N, H)
        dh_train = dh_next.dot(Whh) + dy.dot(Why.T) #(N, H)*(H, H) * (N,C) * (H,C)^T = (N, H)
        dh_next = dh_train
        # nonlinear layer grad
        dh_lin = (1 - h_train[t]**2) * dh_train # (N, H)
        # linear grad. dW db not depend on t, but need sum all t up
        dWhx += x_train[t].T.dot(dh_lin) # (N, C)^T * (N, H) = (C, H)
        dWhh += h_train[t-1].T.dot(dh_lin) # (N, H)*(N, H)=(H, H)
        dbx += dh_lin #(N(1), H)
        #dx[t] don't need renew
    return loss, dWhy, dWhx, dWhh, dby, dbx, h_train[-1]

def adagrad(param_list, dparam_list):
    mWhx, mWhh, mWhy = np.zeros_like(Whx), np.zeros_like(Whh), np.zeros_like(Why)
    mbx, mby = np.zeros_like(bx), np.zeros_like(by)
    # memory variables for Adagrad
    # perform parameter update with Adagrad
    for param, dparam, mem in zip([Whx, Whh, Why, bx, by], 
                                [dWhx, dWhh, dWhy, dbx, dby], 
                                [mWhx, mWhh, mWhy, mbx, mby]):
        mem += dparam * dparam
        param += -lr * dparam / np.sqrt(mem + 1e-8) # adagrad update
    return Why, Whx, Whh, by, bx

In [210]:
# input data return 1 vocab corpus, 2, vocab sets

#voc_corpus = open('./simple_text.txt', 'r').read()
#voc_sets = set(word for word in voc_corpus)
#voc_sets = list(set(word for word in voc_corpus))

# split = [voc.lower().split("\s|(?<!\d)[,.](?!\d)") for voc in voc_corpus]
# v = [v for s in voc_corpus for v in s]
# print(split, v)

# recast into sentence or vocabs
#with open('simple_text.txt','r') as file:
with open('truth.txt','r') as file:
    #vvv = [voc for senten in file for voc in senten.lower().split('\n')]
    voc_corpus = [voc for senten in file for voc in senten.lower().replace(',',' ').replace('.',' ').split()]
    
voc_sets = list(set(voc for voc in voc_corpus))
#print(voc_sets, voc_corpus)



voc_corpus_size, voc_sets_size = len(voc_corpus), len(voc_sets)

#num_voc_sets = len(voc_sets)
# indexing
ix_voc = {i:w for i, w in enumerate(voc_sets)}
voc_ix = {w:i for i, w in enumerate(voc_sets)}




############# Training time #####################
# hyperparameter setting
hidden_size = 100
lr = 1e-1
seq_l = 30 # every time input length
# set weight matrix
Whx = np.random.randn(voc_sets_size, hidden_size)#C, H
Whh = np.random.randn(hidden_size, hidden_size)#H, H
Why = np.random.randn(hidden_size, voc_sets_size)#H, C
bx = np.random.randn(1, hidden_size)# H,
by = np.random.randn(1, voc_sets_size)# C,
h_train, h_lin, x_train, y_train, prob_train = {}, {}, {}, {}, {}
# dh dy don't need store, so just use list
#dh_train, dh_lin, dy = {}, {}, {}
# inputs vocab sequence and target vocab sequece
# all are index (integer)
hprev = np.zeros([hidden_size, 1])
train_iter = 1000
delta_loss = 100
loss0 = 0
#while delta_loss<10:
for num in range(train_iter):
    for i in range(0, len(voc_corpus), seq_l):
        if i+seq_l+1>=len(voc_corpus):
            break
        #print(voc_corpus[i:i+seq_l])
        inputs = [voc_ix[vocab] for vocab in voc_corpus[i:i+seq_l]]
        targets = [voc_ix[vocab] for vocab in voc_corpus[i+1:i+seq_l+1]]

        loss, dWhy, dWhx, dWhh, dby, dbx, hprev = lossFunc(inputs, targets, hprev)

        # renew hyperparameters: lr
        Why, Whx, Whh, by, bx = adagrad([Whx, Whh, Why, bx, by], [dWhx, dWhh, dWhy, dbx, dby])
        
        delta_loss = np.abs(loss - loss0)
        loss0 = loss

print(loss)



############# Testing time #####################
# predict next words
#def predNext()
# gives 1st words
len_sentence = 30
begin_voc = ix_voc[np.random.randint(0, len(voc_sets))]
#print(begin_vec.shape, begin_voc)
idx0 = voc_ix[begin_voc]
begin_vec = np.zeros([1, len(voc_sets)])
begin_vec[0, idx0] = 1 #OneHot
h0_test = np.zeros([1, hidden_size])
h = h0_test
x0 = begin_vec

sentence = [begin_voc]
#sentence = []
# predict one sentence
for t in range(len_sentence):
    #print(type(x0), type(h))
    h = np.tanh(x0.dot(Whx) + h.dot(Whh) + bx)
    y = h.dot(Why) + by
    p = np.exp(y)/np.sum(np.exp(y))
    idx = np.argmax(p)
    # construct x0 vector
    x0 = np.zeros([1, len(voc_sets)])
    x0[0, idx] = 1
    next_voc = ix_voc[idx]
    #print(next_voc)
    sentence.append(next_voc)
    #sentence.append()
    
txt = ' '.join(word for word in sentence)
print( '----\n %s \n----' % (txt))
#print(sentence)


[[1.13907905e-06 1.15839150e-09 2.18375671e-11 7.25602343e-07
  1.26967877e-04 1.72665766e-10 2.50856819e-09 1.28943611e-05
  9.66020568e-06 2.04136467e-06 1.47336792e-07 6.31556275e-04
  1.91366968e-08 1.34611755e-10 1.08048816e-09 8.36087303e-09
  2.25057973e-05 9.84160690e-05 3.64985340e-02 2.06277957e-04
  7.00461309e-12 9.07121111e-06 3.45084577e-09 2.98117801e-04
  3.89544481e-09 8.68118690e-01 1.38396447e-13 8.94184939e-02
  1.07273916e-04 7.81898556e-10 7.45207136e-09 2.03312521e-06
  3.68919648e-03 5.09265848e-05 6.94846085e-04 3.72895962e-07
  6.35973830e-08]]
[[2.76824200e-10 1.27146026e-10 8.24640158e-12 1.24992083e-09
  5.26098769e-09 1.16388695e-10 2.57159668e-09 1.14130079e-08
  1.18534767e-08 1.49111872e-18 8.27220693e-06 5.31642019e-03
  7.94971445e-13 8.89521217e-12 4.31671642e-06 1.14413972e-12
  1.61122990e-08 9.26279742e-18 1.21346305e-04 1.73491270e-16
  8.89364923e-01 7.90761149e-11 1.18722839e-07 1.48855675e-11
  4.98086978e-02 2.10257881e-13 1.73551157e-08 5.43

[[2.18204555e-05 1.75983186e-10 1.49189576e-10 1.32830170e-04
  1.65165889e-05 1.11027174e-09 4.69281298e-06 1.48433439e-06
  2.85735673e-04 3.02550187e-05 2.70553172e-07 2.52572782e-04
  1.55553806e-08 6.79557471e-09 7.01508437e-09 1.42745566e-09
  2.49292481e-05 1.95916756e-06 1.07156056e-03 3.60186966e-02
  1.90416341e-13 4.31868457e-05 1.34705832e-10 5.77977700e-07
  6.52087739e-10 8.95141644e-01 1.03199730e-13 2.78115851e-02
  3.61642294e-07 3.06974311e-11 1.14427696e-09 7.79945997e-07
  5.79690376e-04 5.40116764e-06 3.85339346e-02 1.94568029e-05
  2.32377233e-08]]
[[7.33239739e-01 4.18774823e-15 1.35260375e-11 2.59969182e-10
  3.71510513e-15 7.21647789e-10 9.04875327e-09 8.69108589e-13
  7.01662839e-13 7.10434059e-13 9.98725775e-12 1.36942037e-06
  1.00896055e-14 6.07815850e-08 6.36677348e-07 6.80910317e-11
  1.58072124e-12 1.14366726e-14 7.05236362e-16 3.51518149e-13
  2.59043283e-11 1.70716404e-13 4.72987463e-20 1.22693109e-11
  3.48993402e-07 3.67211981e-12 2.88956827e-07 3.05

  2.15977406e-08]]
[[6.02120991e-08 3.29645798e-12 5.07988082e-04 8.16860795e-05
  7.00871447e-16 1.09948993e-07 2.83512262e-01 6.17793742e-09
  1.66530483e-11 3.23665317e-07 4.84199016e-07 7.06282860e-11
  1.64253614e-08 1.09122556e-06 7.64452914e-10 2.65498951e-08
  1.51926737e-05 2.00121526e-08 9.88806849e-07 2.04468006e-07
  3.06045743e-14 1.16059833e-06 9.53726415e-08 2.50887019e-12
  1.68172961e-04 2.66638610e-08 8.66623467e-11 5.33430030e-12
  1.12268503e-10 7.85663850e-05 5.74362080e-10 6.73782376e-01
  7.79844585e-03 4.96170195e-13 3.40506790e-02 1.47418653e-08
  1.36297646e-14]]
[[5.04574937e-11 4.60016585e-09 1.42458671e-05 7.91249628e-08
  2.12725167e-04 1.01664809e-11 1.18669698e-06 2.51823819e-04
  2.21041520e-14 3.35690758e-05 2.11697608e-08 1.71868009e-18
  2.03971975e-07 1.09407059e-06 3.72152301e-07 1.05344809e-07
  6.37081053e-10 1.98190546e-07 1.60025441e-05 5.33551530e-08
  8.46833632e-07 9.92444851e-05 8.25644459e-09 6.80613630e-04
  4.09261991e-12 5.75793237e-02 

[[1.24900689e-05 2.05353433e-11 8.70056187e-09 1.75667745e-03
  2.76600843e-04 1.72587061e-03 3.32438286e-06 4.25234954e-06
  6.82932054e-08 1.23019585e-16 4.77045997e-14 3.34649920e-16
  5.41488872e-16 9.31283867e-04 2.52697189e-14 5.91259566e-13
  1.71481773e-04 6.02100507e-09 2.61184671e-10 4.00770913e-04
  2.44047835e-13 9.52736831e-12 2.33454508e-13 3.94602082e-13
  5.17864188e-16 2.15202715e-01 6.36320202e-10 1.14866886e-02
  2.24191542e-07 1.41293974e-11 6.37273251e-05 6.83590239e-08
  3.60334643e-02 2.88451890e-09 1.86995793e-06 7.31928403e-01
  1.00643270e-10]]
[[1.94444256e-10 2.24547379e-11 9.79733995e-01 2.00069353e-02
  3.04688797e-06 2.27594241e-10 1.94891501e-05 5.41116618e-10
  1.03657908e-17 1.18123195e-10 1.09295692e-11 8.91465770e-13
  7.10626087e-11 1.08851583e-06 1.27004925e-12 1.78079426e-09
  2.22072117e-04 6.79495406e-14 3.79635221e-10 2.73031585e-06
  9.16205449e-18 1.82392261e-16 3.26248647e-12 1.57321071e-07
  2.68794846e-10 9.69630994e-09 1.88015637e-09 1.04

  2.16783269e-02]]
[[2.08865066e-12 1.28068030e-01 1.25120226e-08 8.15790040e-15
  2.19717413e-13 9.67823614e-05 2.98065900e-07 4.57110588e-11
  1.24732986e-10 5.93325426e-05 1.65235834e-13 6.38023886e-08
  3.44876896e-11 4.76144074e-09 6.61621256e-12 2.79353412e-05
  4.86356711e-12 5.76388367e-13 2.70232603e-06 1.18834205e-10
  6.41117295e-11 1.94853439e-11 6.61502406e-11 1.03227016e-09
  1.65707259e-11 2.15017828e-13 5.46528052e-08 6.03885478e-05
  2.84963815e-10 6.40509124e-15 3.21515009e-11 9.51981309e-13
  1.64196108e-06 1.32609875e-09 9.32189221e-02 5.24233018e-19
  7.78463828e-01]]
[[1.21844844e-13 1.66793860e-08 1.36853272e-12 4.31687440e-10
  1.20545198e-09 2.74150168e-09 1.16627774e-10 1.64219459e-07
  1.27378587e-13 4.73337568e-15 1.07091357e-13 6.07145514e-14
  6.85588891e-16 8.01752126e-07 1.17452258e-07 2.38693986e-12
  1.03284382e-12 1.25604498e-13 1.16729516e-14 3.86949062e-10
  1.69580031e-17 2.54975325e-10 2.80877138e-21 7.69907955e-07
  1.14086074e-13 2.65964841e-09 

...

  6.77776450e-21]]
[[8.62133878e-15 1.62050297e-05 1.09031944e-15 2.15584284e-24
  5.03581036e-04 8.22986247e-23 1.40650363e-03 2.12378932e-22
  3.98208265e-16 2.54951422e-16 1.03728298e-11 3.87796929e-10
  1.80038878e-12 7.85742363e-14 8.92396293e-18 2.00875773e-12
  4.35378155e-08 1.78169323e-07 5.12849482e-03 9.66920949e-17
  3.71536594e-13 5.81119717e-17 4.01936578e-15 3.50714776e-09
  4.49217099e-10 3.55222304e-13 7.21767536e-07 9.92942895e-01
  5.53621443e-15 2.59587829e-12 1.88860376e-10 8.86303782e-12
  6.72090662e-08 2.48508391e-12 4.47089092e-09 1.30073637e-06
  1.27238590e-15]]
[[1.14402861e-17 1.15984100e-11 3.83603344e-22 4.22262949e-31
  2.07555508e-13 7.37976813e-24 1.53500910e-09 1.20879041e-31
  2.61235273e-16 3.94756486e-20 3.26887541e-17 4.43920445e-17
  1.82619250e-16 3.61638626e-15 4.02142112e-26 3.29817691e-17
  1.30588908e-20 1.01861318e-15 9.99999742e-01 1.81552710e-21
  2.96574173e-18 1.70332835e-17 2.82220297e-17 2.51022555e-20
  6.42141515e-15 2.97528002e-27 

[[1.98653047e-13 5.16081876e-06 4.35357658e-26 7.66305061e-25
  1.10571696e-10 5.56358747e-18 8.99488208e-08 3.77997416e-22
  9.67296292e-16 2.23189408e-17 3.08326287e-12 4.89020348e-11
  7.75007820e-13 6.22991331e-13 1.53820088e-20 1.86023101e-12
  5.44252271e-13 6.67243661e-14 3.17313187e-03 4.12455379e-23
  9.39943269e-13 1.83132498e-05 2.17646348e-13 7.67375277e-14
  2.19075813e-10 4.74098772e-17 5.04544101e-12 1.34209141e-05
  1.99160438e-03 3.08318137e-10 2.18533938e-11 5.49110593e-12
  4.76219817e-16 2.63036406e-12 9.05953616e-14 9.94798278e-01
  1.47563325e-14]]
[[4.35913057e-13 7.86839376e-07 1.34685948e-25 1.28847184e-19
  6.25829033e-11 3.14406118e-16 8.86586062e-11 1.19476202e-21
  1.24908166e-09 2.23532829e-14 2.24431228e-12 2.44047279e-12
  1.60727310e-12 3.26290999e-11 2.73851641e-22 6.11238631e-12
  1.02947806e-19 2.19984637e-13 1.32349989e-02 4.89300638e-23
  3.03410532e-13 4.21839435e-06 3.08045938e-12 8.47952123e-13
  1.27839226e-10 3.34715873e-26 9.51115125e-20 1.00

  5.12817237e-15]]
[[5.90602665e-14 1.67637749e-08 5.60428567e-20 1.02652163e-16
  8.57474182e-07 7.40401947e-17 1.02752065e-06 2.27571751e-24
  2.41919350e-09 1.66081718e-10 5.08550538e-13 1.82987273e-11
  1.59809096e-12 2.31340797e-09 1.42910569e-21 2.02252883e-11
  1.43674784e-24 6.26056026e-15 8.27938309e-04 3.70109105e-24
  7.31071214e-13 2.17944735e-10 1.27799510e-11 1.30735456e-15
  3.01849721e-09 2.70924484e-24 1.78628068e-17 6.43156693e-13
  3.49958073e-07 2.19659909e-10 7.00658095e-11 9.97237261e-01
  1.46386996e-23 1.50976682e-11 1.49957860e-18 1.93254041e-03
  4.29832479e-11]]
[[7.30061279e-13 3.66258906e-04 2.69069206e-17 2.52320074e-11
  1.62615001e-02 5.76116752e-12 7.90019542e-05 1.33980980e-17
  9.91043763e-05 2.18067867e-05 9.30714301e-08 2.46771802e-06
  4.76811425e-08 3.21867761e-08 8.16493457e-18 1.74355404e-07
  4.55209594e-25 9.23195203e-10 2.23163367e-01 8.02092270e-24
  6.26293268e-09 8.36101198e-05 9.50627904e-08 3.30202765e-08
  5.11134915e-06 7.55399481e-25 

[[2.78868992e-24 5.35645525e-13 1.57638291e-02 4.47840477e-13
  2.58271162e-06 1.48688574e-14 6.51466666e-15 9.84222776e-01
  6.50330189e-11 4.30527646e-16 3.33726523e-25 3.40394305e-23
  3.73066919e-23 3.89586481e-24 8.44191304e-10 8.13165920e-24
  9.69661606e-08 2.38618835e-25 2.45639375e-21 3.94810494e-18
  9.05299753e-25 3.12934422e-21 1.34417721e-22 1.79972940e-15
  5.92148887e-23 6.75886376e-06 8.14122426e-11 4.61974508e-12
  3.72387104e-13 1.02034572e-24 5.26111321e-23 6.75166196e-25
  3.92975487e-06 1.97993897e-23 2.58202872e-08 3.12945610e-23
  1.22225048e-14]]
[[3.76300664e-23 7.21138078e-13 7.50498460e-06 5.79655874e-11
  9.03423632e-10 1.24048200e-19 2.07192219e-13 1.98975743e-07
  3.45128920e-08 8.83785904e-22 4.45613426e-24 2.16971904e-23
  8.00270632e-25 1.33352695e-22 6.72663911e-16 2.59877672e-24
  2.83068170e-09 7.05211328e-24 8.41783940e-11 1.46123523e-13
  1.46869324e-25 3.77106756e-26 3.34436050e-23 1.83179227e-19
  2.26037129e-22 4.45590964e-05 1.61803458e-07 6.76

KeyboardInterrupt: 